In [90]:
# pysw4_vs_profile.py
# Queries rfile to properties for vs profile


import pySW4 as sw4
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd

import sys
import os

In [91]:
#f = '/Users/rodgers7/WORK/EQ_SIMULATIONS/USGS_MODEL/USGSBayAreaVM-08.3.0-corder.rfile'
#f = '/Users/taira/work/USGS_RFILE/USGSBayAreaVM-08.3.0-corder.rfile'
f = '/ref/noise01/taira/USGSBayArea/USGSBayAreaVM-08.3.0-corder.rfile'



In [92]:
model = sw4.prep.rfileIO.read(f, block_number='all', verbose=True)

Model information :
----------------- :
         Filename : /ref/noise01/taira/USGSBayArea/USGSBayAreaVM-08.3.0-corder.rfile
            lon 0 : -122.5623650935
            lat 0 : 39.17450494695
          Azimuth : 143.6380001671
     Proj4 string : b'+proj=tmerc +datum=NAD83 +units=m +lon_0=-123.0 +lat_0=35.0 +scale=0.9996'
 Number of blocks : 5

Block information :
----------------- :
           Number : 1
  Horizontal h, m : 100.0
    Vertical h, m : 25.0
           z 0, m : 0.0
               ni : 2897
               nj : 1401
               nk : 1
               nc : 1

Block information :
----------------- :
           Number : 2
  Horizontal h, m : 100.0
    Vertical h, m : 25.0
           z 0, m : -1437.5
               ni : 2897
               nj : 1401
               nk : 74
               nc : 5

Block information :
----------------- :
           Number : 3
  Horizontal h, m : 200.0
    Vertical h, m : 50.0
           z 0, m : 387.5
               ni : 1449
               n

In [93]:
# Oakland
place = 'Oakland'
lat, lon = 37.8103, -122.275
# Orinda
#place = 'Orinda'
#lat, lon = 37.8743, -122.165

#place = "AR2022"
#lat, lon = 37.30983 -121.68157 

place = 'outside'
lat, lon = 40, -124
lat, lon = 37, -120

place = 'BK.BKS'
lat, lon =  37.87622, -122.23558 

In [94]:
#[noise:/home/bsl/taira/dc6_doc/BK.info 145] less BK.stations | awk '{print $2"."$1","$3","$4}' | sort -n | uniq -c | awk 'BEGIN{print "net.sta,lat,lon";}{print $2}' 
net = "BK"
net_info_dir = "/work/dc6/ftp/pub/doc/"+net+".info"
station_file = net_info_dir+"/"+net+".stations"
print("# station_file = ", station_file)





# station_file =  /work/dc6/ftp/pub/doc/BK.info/BK.stations


In [95]:

def cal_1d_profile(place, property, model, lat, lon, csv_dir = "sfba_1d_profile"):
    
    
    if not os.path.exists(csv_dir):
        os.makedirs(csv_dir)

    csv_fi = csv_dir+"/"+place+"."+property+".csv"
    print("csv_fi = {0}".format(csv_fi))

    x, y = sw4.utils.geographic2cartesian(proj4=model.proj_str.decode('utf-8'), 
        lon0=model.lon0, lat0=model.lat0, az=model.az, 
        m_per_lat=None, m_per_lon=None, 
        lon=lon, lat=lat, x=None, y=None)
    
    z, property_out = model.get_z_profile(x/1000, y/1000, property=property)
    #vs = np.ma.masked_equal(vs, -999)
    model = np.vstack( (z, property_out) ).T
    model = model[ np.where( model[:,1] > 0 ) ]
    d = { 'z' : model[:,0] , property: model[:,1]}
    df = pd.DataFrame(d)
    df.to_csv(csv_fi)



In [96]:
# need to get BK_list.csv first
#[suture:/data/seis01/taira/Instrumentation/python_work 45] cat '/work/dc6/ftp/pub/doc/BK.info/BK.stations' | awk '{print $2"."$1","$3","$4}' | sort -n | uniq -c | awk 'BEGIN{print "net.sta,lat,lon";}{print $2}' >! BK_list.csv
station_csv = net+"_list.csv"
print("station_csv = {0}".format(station_csv))
df_station = pd.read_csv(station_csv, header=0) 
print("df_station = {0}".format(df_station))



station_csv = BK_list.csv
df_station =      net.sta      lat       lon
0    BK.AASB  38.4303 -121.1098
1    BK.ADAM  38.7514 -122.3341
2    BK.ALVW  37.0491 -120.4714
3    BK.AONC  39.9398 -122.0608
4     BK.ARC  40.8777 -124.0774
..       ...      ...       ...
184  BK.WROK  35.4453 -120.8802
185  BK.WSRE  36.3354 -120.1172
186   BK.YBH  41.7320 -122.7104
187  BK.YBIB  37.8142 -122.3592
188  BK.YUBA  39.3376 -120.5372

[189 rows x 3 columns]


In [101]:
properties = ["vs", "vp"]
properties = ["vs", "vp", "rho", "qp", "qs"]

property = properties[0]
print("property = {0}".format(property))

property = vs


In [102]:
df_station['lat']

0      38.4303
1      38.7514
2      37.0491
3      39.9398
4      40.8777
        ...   
184    35.4453
185    36.3354
186    41.7320
187    37.8142
188    39.3376
Name: lat, Length: 189, dtype: float64

In [103]:
len(df_station['lat'])

189

In [104]:
for i, lat in enumerate(df_station['lat']):
#for i, lat in enumerate(df_station):
#for i in range(len(df_station['lat']):
    #print("i = {0} lat = {1}".format(i, lat))

    for property in properties:
        cal_1d_profile(df_station['net.sta'][i], property, model, df_station['lat'][i], df_station['lon'][i], csv_dir = "sfba_1d_profile")
    
    #sys.exit()


csv_fi = sfba_1d_profile/BK.AASB.vs.csv
csv_fi = sfba_1d_profile/BK.AASB.vp.csv
csv_fi = sfba_1d_profile/BK.AASB.rho.csv
csv_fi = sfba_1d_profile/BK.AASB.qp.csv
csv_fi = sfba_1d_profile/BK.AASB.qs.csv
csv_fi = sfba_1d_profile/BK.ADAM.vs.csv
csv_fi = sfba_1d_profile/BK.ADAM.vp.csv
csv_fi = sfba_1d_profile/BK.ADAM.rho.csv
csv_fi = sfba_1d_profile/BK.ADAM.qp.csv
csv_fi = sfba_1d_profile/BK.ADAM.qs.csv
csv_fi = sfba_1d_profile/BK.ALVW.vs.csv
csv_fi = sfba_1d_profile/BK.ALVW.vp.csv
csv_fi = sfba_1d_profile/BK.ALVW.rho.csv
csv_fi = sfba_1d_profile/BK.ALVW.qp.csv
csv_fi = sfba_1d_profile/BK.ALVW.qs.csv
csv_fi = sfba_1d_profile/BK.AONC.vs.csv
csv_fi = sfba_1d_profile/BK.AONC.vp.csv
csv_fi = sfba_1d_profile/BK.AONC.rho.csv
csv_fi = sfba_1d_profile/BK.AONC.qp.csv
csv_fi = sfba_1d_profile/BK.AONC.qs.csv


/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:

csv_fi = sfba_1d_profile/BK.ARC.vs.csv
csv_fi = sfba_1d_profile/BK.ARC.vp.csv
csv_fi = sfba_1d_profile/BK.ARC.rho.csv
csv_fi = sfba_1d_profile/BK.ARC.qp.csv
csv_fi = sfba_1d_profile/BK.ARC.qs.csv
csv_fi = sfba_1d_profile/BK.ATP.vs.csv
csv_fi = sfba_1d_profile/BK.ATP.vp.csv
csv_fi = sfba_1d_profile/BK.ATP.rho.csv
csv_fi = sfba_1d_profile/BK.ATP.qp.csv
csv_fi = sfba_1d_profile/BK.ATP.qs.csv
csv_fi = sfba_1d_profile/BK.AZUL.vs.csv
csv_fi = sfba_1d_profile/BK.AZUL.vp.csv
csv_fi = sfba_1d_profile/BK.AZUL.rho.csv
csv_fi = sfba_1d_profile/BK.AZUL.qp.csv
csv_fi = sfba_1d_profile/BK.AZUL.qs.csv
csv_fi = sfba_1d_profile/BK.BABI.vs.csv
csv_fi = sfba_1d_profile/BK.BABI.vp.csv
csv_fi = sfba_1d_profile/BK.BABI.rho.csv
csv_fi = sfba_1d_profile/BK.BABI.qp.csv
csv_fi = sfba_1d_profile/BK.BABI.qs.csv
csv_fi = sfba_1d_profile/BK.BAKR.vs.csv


/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:

csv_fi = sfba_1d_profile/BK.BAKR.vp.csv
csv_fi = sfba_1d_profile/BK.BAKR.rho.csv
csv_fi = sfba_1d_profile/BK.BAKR.qp.csv
csv_fi = sfba_1d_profile/BK.BAKR.qs.csv
csv_fi = sfba_1d_profile/BK.BARR.vs.csv
csv_fi = sfba_1d_profile/BK.BARR.vp.csv
csv_fi = sfba_1d_profile/BK.BARR.rho.csv
csv_fi = sfba_1d_profile/BK.BARR.qp.csv
csv_fi = sfba_1d_profile/BK.BARR.qs.csv
csv_fi = sfba_1d_profile/BK.BAYL.vs.csv
csv_fi = sfba_1d_profile/BK.BAYL.vp.csv
csv_fi = sfba_1d_profile/BK.BAYL.rho.csv
csv_fi = sfba_1d_profile/BK.BAYL.qp.csv
csv_fi = sfba_1d_profile/BK.BAYL.qs.csv
csv_fi = sfba_1d_profile/BK.BBEB.vs.csv
csv_fi = sfba_1d_profile/BK.BBEB.vp.csv
csv_fi = sfba_1d_profile/BK.BBEB.rho.csv
csv_fi = sfba_1d_profile/BK.BBEB.qp.csv
csv_fi = sfba_1d_profile/BK.BBEB.qs.csv
csv_fi = sfba_1d_profile/BK.BCCR.vs.csv


...

/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:

csv_fi = sfba_1d_profile/BK.WINE.qs.csv
csv_fi = sfba_1d_profile/BK.WLKR.vs.csv
csv_fi = sfba_1d_profile/BK.WLKR.vp.csv
csv_fi = sfba_1d_profile/BK.WLKR.rho.csv
csv_fi = sfba_1d_profile/BK.WLKR.qp.csv
csv_fi = sfba_1d_profile/BK.WLKR.qs.csv
csv_fi = sfba_1d_profile/BK.WROK.vs.csv
csv_fi = sfba_1d_profile/BK.WROK.vp.csv
csv_fi = sfba_1d_profile/BK.WROK.rho.csv
csv_fi = sfba_1d_profile/BK.WROK.qp.csv
csv_fi = sfba_1d_profile/BK.WROK.qs.csv
csv_fi = sfba_1d_profile/BK.WSRE.vs.csv
csv_fi = sfba_1d_profile/BK.WSRE.vp.csv
csv_fi = sfba_1d_profile/BK.WSRE.rho.csv
csv_fi = sfba_1d_profile/BK.WSRE.qp.csv
csv_fi = sfba_1d_profile/BK.WSRE.qs.csv
csv_fi = sfba_1d_profile/BK.YBH.vs.csv
csv_fi = sfba_1d_profile/BK.YBH.vp.csv
csv_fi = sfba_1d_profile/BK.YBH.rho.csv
csv_fi = sfba_1d_profile/BK.YBH.qp.csv
csv_fi = sfba_1d_profile/BK.YBH.qs.csv
csv_fi = sfba_1d_profile/BK.YBIB.vs.csv


/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:

csv_fi = sfba_1d_profile/BK.YBIB.vp.csv
csv_fi = sfba_1d_profile/BK.YBIB.rho.csv
csv_fi = sfba_1d_profile/BK.YBIB.qp.csv
csv_fi = sfba_1d_profile/BK.YBIB.qs.csv
csv_fi = sfba_1d_profile/BK.YUBA.vs.csv
csv_fi = sfba_1d_profile/BK.YUBA.vp.csv
csv_fi = sfba_1d_profile/BK.YUBA.rho.csv
csv_fi = sfba_1d_profile/BK.YUBA.qp.csv
csv_fi = sfba_1d_profile/BK.YUBA.qs.csv


/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/data/seis01/taira/Anaconda_x86_linux_py3_rev/envs/sw4/lib/python3.8/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:

In [ ]:
# remove no data site
# [suture:/home/bsl/taira/hydro/Instrumentation/python_work/sfba_1d_profile 244] ls -lsrt *qs*csv | awk '{if($6<10)print $0}' | awk '{print $10}' | sed 's/.qs.csv//g' | awk '{printf("%s* ",$1);}'
# BK.ALVW* BK.AZUL* BK.BABI* BK.BIGV* BK.BRAD* BK.BRIT* BK.CCOR* BK.CGRV* BK.CLRV* BK.DIAZ* BK.DRYC* BK.EAGL* BK.ELFS* BK.GRPK* BK.HAPY* BK.HAS2* BK.HAST* BK.HATC* BK.HELL* BK.HULI* BK.HUMO* BK.KARE* BK.KCC* BK.LAND* BK.LCUV* BK.LEGD* BK.LGMB* BK.LIND* BK.LITV* BK.LSIB* BK.MILL* BK.MIN* BK.MMI* BK.MNLT* BK.MOD* BK.MOGU* BK.MZTA* BK.OVRO* BK.PABC* BK.PIT6* BK.PKD1* BK.PKD2* BK.PKD* BK.PORC* BK.PVSP* BK.RAMR* BK.RAVE* BK.RIMR* BK.SAGE* BK.SANG* BK.SCZ* BK.SHEP* BK.SIGP* BK.TCAS* BK.TCHL* BK.THIS* BK.TOLH* BK.TRAM* BK.TRAY* BK.TSCN* BK.TSCS* BK.TULE* BK.WHCL* BK.WHMT* BK.WINE* BK.WROK* BK.WSRE* BK.YBH* [suture:/home/bsl/taira/hydro/Instrumentation/python_work/sfba_1d_profile 245] 
